In [0]:
pip install spacy

Python interpreter will be restarted.
Python interpreter will be restarted.


In [0]:
!python -m spacy download en_core_web_sm

     |█████████                       | 

*** WARNING: max output size exceeded, skipping output. ***

     |████████████████████████████████| 12.8 MB 4.4 MB/s 
You should consider upgrading via the '/local_disk0/.ephemeral_nfs/envs/pythonEnv-8cdf8806-7d7d-4067-994f-19368b0be9fd/bin/python -m pip install --upgrade pip' command.
✔ Download and installation successful
You can now load the package via spacy.load('en_core_web_sm')


In [0]:
from pyspark.sql.functions import count, to_date, date_format, year, col, avg, countDistinct, sum, lit, length, udf
import pandas as pd
from pyspark.sql.types import StringType
import spacy

In [0]:
file_path = "/FileStore/tables/filtered_reviews_part_2.csv"

In [0]:
df = spark.read.csv(file_path, header=True, inferSchema=True, multiLine=True, escape='"')

In [0]:
df.limit(5).show()

+--------------------+--------------------+--------------------+-----+------+-----+----+--------------------+-------------------+
|           review_id|             user_id|         business_id|stars|useful|funny|cool|                text|               date|
+--------------------+--------------------+--------------------+-----+------+-----+----+--------------------+-------------------+
|l3-NvFb9CZ5kyozZi...|NngzzY7_E1OciTrIo...|NDzQFHW671hbB-aAr...|  3.0|     0|    0|   0|Food is overprice...|2021-09-30 21:42:01|
|4tkZGQPmhCBpgNDZd...|HYozx6QC9nOHb6VeX...|jRpK8oG_8QKaPGaaK...|  4.0|     0|    0|   0|Great pizza, good...|2014-08-09 17:24:52|
|_-il7JuW4Cvl1t8mH...|a1qd8VKm8ideNJZT1...|ehqT-Pek95bMYQKx5...|  5.0|     0|    0|   0|This was a great ...|2020-12-13 19:04:52|
|vY63xTGQsxU8YzWlh...|Mu7efJ4vtjTSSRm0G...|ShBW2Fx5RvPqYxwRD...|  5.0|     0|    0|   0|I mentioned to th...|2018-07-15 02:09:23|
|lMugSxDDDdJF7crcL...|weVmDqYqax565OAQ9...|l4lfhwS8dEhy3MZ3A...|  1.0|     2|    1|   1|St

In [0]:
df1 = df.select("review_id", "user_id", "business_id", "stars", "useful", "funny", "cool", "date")

In [0]:
# Convert the "date" column to a DateType
df1 = df1.withColumn("date", to_date(df1["date"]))

# Extract the year and month from the "date" column
df1 = df1.withColumn("year", year(df1["date"]))
df1 = df1.withColumn("year_month", date_format(df1["date"], "yyyy-MM"))

In [0]:
# Group the data by date and count the number of reviews for each date
reviews_count_by_month = df1.groupBy("year_month").agg(count("*").alias("review_count"))

In [0]:
reviews_count_by_month.display()

year_month review_count 2020-06 5020 2013-05 4276 2020-12 5338 2019-10 9494 2009-07 999 2018-10 9475 2013-09 4515 2020-02 9256 2010-08 1951 2007-05 134 2009-01 844 2021-07 8053 2017-09 8671 2008-02 326 2005-07 33 2005-09 8 2013-12 4635 2019-11 8473 2006-07 60 2021-04 7064 2010-11 1859 2013-06 4126 2006-05 30 2005-12 11 2008-09 606 2010-02 1397 2007-08 213 2006-04 30 2005-02 1 2017-10 8925 2006-09 62 2021-06 7752 2010-04 1412 2016-02 8849 2019-03 11716 2018-06 10822 2017-05 10039 2011-05 2740 2017-11 8313 2015-05 8009 2018-03 11349 2012-08 3334 2020-05 3957 2015-12 7333 2012-02 3296 2006-03 26 2010-03 1560 2021-11 5987 2012-04 3260 2007-07 219 2010-01 1637 2017-03 9503 2018-02 9256 2016-12 7422 2010-09 1838 2016-09 7754 2017-08 9549 2012-05 3207 2005-10 3 2021-03 7012 2006-08 59 2009-10 903 2008-08 728 2021-02 5613 2007-12 178 2016-03 9212 2019-07 11134 2017-06 9893 2016-10 7930 2010-06 1495 2005-11 10 2012-12 3270 2008-05 551 2012-07 3555 2021-12 6459 2017-02 8403 2021-10 6518 2014-01 5413 2011-03 2797 2017-04 9674 2020-11 5533 2018-05 10571 2010-07 1818 2006-10 62 2015-02 6988 2015-08 9004 2005-05 16 2018-08 10427 2014-03 5904 2014-08 6812 2017-07 10388 2007-09 215 2011-01 2560 2013-11 4578 2014-02 4747 2012-01 3677 2021-05 7777 2008-06 604 2009-08 1068 2015-10 8022 2019-05 10701 2008-04 470 2020-07 5846 2019-08 10873 2006-02 22 2011-11 2660 2015-11 7527 2013-02 3672 2012-11 3158 2005-06 11 2019-01 10108 2008-12 580 2016-05 9043 2014-09 5888 2007-01 117 2007-02 198 2019-09 9750 2006-11 67 2012-06 3370 2013-07 4399 2009-11 952 2014-05 6017 2015-01 7404 2012-09 3142 2016-04 8576 2006-01 28 2020-03 5990 2011-08 3086 2007-10 201 2017-12 8324 2018-11 8864 2006-12 78 2005-04 4 2011-04 2675 2016-11 7246 2011-09 2728 2013-08 4910 2021-08 7495 2020-01 9221 2011-07 3130 2011-10 2566 2019-06 10924 2008-11 613 2014-11 5875 2019-04 10228 2020-09 6274 2018-12 9555 2009-12 1005 2016-01 8951 2016-07 9509 2016-06 8760 2015-07 8842 2014-04 5566 2007-06 170 2008-07 725 2014-10 5943 2015-09 7765 2010-05 1494 2011-02 2562 2011-06 2720 2009-09 936 2009-05 850 2019-12 8628 2014-12 6062 2013-03 4279 2007-03 146 2014-06 5933 2013-10 4575 2020-08 6324 2012-10 3228 2010-12 1907 2014-07 6827 2018-04 10638 2018-01 9468 2011-12 2594 2007-11 197 2005-08 13 2009-04 812 2005-03 7 2015-06 7836 2009-03 921 2015-04 7626 2013-01 4266 2019-02 9735 2021-01 5971 2008-01 310 2016-08 8747 2020-04 2674 2010-10 1823 2020-10 6344 2021-09 6038 2009-06 887 2018-09 9600 2022-01 4121 2013-04 4047 2017-01 8824 2018-07 12203 2012-03 3386 2015-03 8002 2009-02 762 2007-04 162 2008-03 369 2008-10 599 2006-06 34

Databricks visualization. Run in Databricks to view.

In [0]:
stars_count = df1.groupBy("stars").agg(count("*").alias("star_count"))

# Calculate the total count of all reviews
total_count = df1.count()

# Add a new column for the percentage of each group
stars_count = stars_count.withColumn("percentage", (col("star_count") / total_count) * 100)

stars_count.display()

stars star_count percentage 1.0 113189 11.979015635616271 4.0 225526 23.86786242689656 3.0 108496 11.482346167929949 2.0 81162 8.589534910794226 5.0 416521 44.081240858762996

Databricks visualization. Run in Databricks to view.

Databricks visualization. Run in Databricks to view.

In [0]:
avg_monthly_rating = df1.groupBy("year_month").agg(avg("stars").alias("average_rating"))
avg_monthly_rating.display()

year_month average_rating 2020-06 3.893824701195219 2013-05 3.6251169317118803 2020-12 3.9439865118021733 2019-10 3.8301032230882663 2009-07 3.630630630630631 2018-10 3.8619525065963063 2013-09 3.704761904761905 2020-02 3.857389801210026 2010-08 3.6945156330087134 2007-05 3.9029850746268657 2009-01 3.741706161137441 2021-07 3.797839314541165 2017-09 3.8011763349094685 2008-02 3.8650306748466257 2005-07 3.696969696969697 2005-09 4.0 2013-12 3.7083063646170444 2019-11 3.792163342381683 2006-07 3.7666666666666666 2021-04 3.795300113250283 2010-11 3.7428725121032813 2013-06 3.6476005816771693 2006-05 4.266666666666667 2005-12 4.0 2008-09 3.7046204620462047 2010-02 3.7172512526843238 2007-08 3.7183098591549295 2006-04 4.1 2005-02 4.0 2017-10 3.8233053221288515 2006-09 4.016129032258065 2021-06 3.84171826625387 2010-04 3.671388101983003 2016-02 3.794553056842581 2019-03 3.836889723455104 2018-06 3.8643503973387543 2017-05 3.823089949198127 2011-05 3.6164233576642335 2017-11 3.8379646337062434 2015-05 3.7457859907603948 2018-03 3.8182218697682617 2012-08 3.6955608878224355 2020-05 3.8471063937326258 2015-12 3.756307104868403 2012-02 3.668992718446602 2006-03 3.576923076923077 2010-03 3.6891025641025643 2021-11 3.8095874394521463 2012-04 3.675153374233129 2007-07 3.7534246575342465 2010-01 3.7018937080024434 2017-03 3.7980637693359993 2018-02 3.8161192739844427 2016-12 3.754109404473188 2010-09 3.735582154515778 2016-09 3.7605107041526953 2017-08 3.870667085558697 2012-05 3.6697848456501405 2005-10 4.333333333333333 2021-03 3.8168853394181403 2006-08 3.7796610169491527 2009-10 3.753045404208195 2008-08 3.754120879120879 2021-02 3.9385355424906465 2007-12 3.7808988764044944 2016-03 3.7912505427702996 2019-07 3.8417460032333395 2017-06 3.8448397857070655 2016-10 3.7931904161412358 2010-06 3.6882943143812708 2005-11 3.7 2012-12 3.644954128440367 2008-05 3.8784029038112524 2012-07 3.669760900140647 2021-12 3.760953708004335 2017-02 3.8053076282280136 2021-10 3.836606320957349 2014-01 3.766857565121005 2011-03 3.6996782266714336 2017-04 3.788401902005375 2020-11 3.929333092354961 2018-05 3.8283038501560873 2010-07 3.6688668866886687 2006-10 3.903225806451613 2015-02 3.737979393245564 2015-08 3.8248556197245667 2005-05 4.25 2018-08 3.836386304785653 2014-03 3.747967479674797 2014-08 3.7451556077510277 2017-07 3.8291297651135925 2007-09 3.972093023255814 2011-01 3.71640625 2013-11 3.700087374399301 2014-02 3.7552138192542657 2012-01 3.689148762578189 2021-05 3.7688054519737686 2008-06 3.73841059602649 2009-08 3.701310861423221 2015-10 3.8057840937422087 2019-05 3.834968694514531 2008-04 3.8361702127659574 2020-07 3.953301402668491 2019-08 3.900119562218339 2006-02 4.2272727272727275 2011-11 3.6646616541353385 2015-11 3.78132057924804 2013-02 3.662037037037037 2012-11 3.674794173527549 2005-06 4.181818181818182 2019-01 3.8766323703996832 2008-12 3.7672413793103448 2016-05 3.774853477828154 2014-09 3.762398097826087 2007-01 3.982905982905983 2007-02 3.712121212121212 2019-09 3.7835897435897436 2006-11 3.671641791044776 2012-06 3.710979228486647 2013-07 3.7233462150488745 2009-11 3.7436974789915967 2014-05 3.7372444739903607 2015-01 3.7975418692598595 2012-09 3.667727562062381 2016-04 3.805387126865672 2006-01 4.142857142857143 2020-03 3.9290484140233723 2011-08 3.683732987686325 2007-10 3.9502487562189055 2017-12 3.781114848630466 2018-11 3.8467960288808665 2006-12 4.243589743589744 2005-04 4.25 2011-04 3.6986915887850467 2016-11 3.8015456803753795 2011-09 3.685850439882698 2013-08 3.6973523421588594 2021-08 3.771447631754503 2020-01 3.8458952391280774 2011-07 3.6849840255591055 2011-10 3.6434138737334374 2019-06 3.8483156352984254 2008-11 3.7650897226753672 2014-11 3.740936170212766 2019-04 3.837602659366445 2020-09 3.9043672298374243 2018-12 3.781475667189953 2009-12 3.6776119402985072 2016-01 3.790861356273042 2016-07 3.801030602587023 2016-06 3.814840182648402 2015-07 3.808866772223479 2014-04 3.7430830039525693 2007-06 3.847058823529412 2

Databricks visualization. Run in Databricks to view.

In [0]:
df1.count()

Out[12]: 944894

In [0]:
df1.select(countDistinct("business_id").alias("unique_businesses")).first()["unique_businesses"]

Out[13]: 49837

In [0]:
df1.select(countDistinct("user_id").alias("unique_users")).first()["unique_users"]

Out[14]: 507858

In [0]:
df1.select([sum(col(c).isNull().cast("int")).alias(c) for c in df1.columns]).show()

+---------+-------+-----------+-----+------+-----+----+----+----+----------+
|review_id|user_id|business_id|stars|useful|funny|cool|date|year|year_month|
+---------+-------+-----------+-----+------+-----+----+----+----+----------+
|        0|      0|          0|    0|     0|    0|   0|   0|   0|         0|
+---------+-------+-----------+-----+------+-----+----+----+----+----------+



In [0]:
duplicate_review_ids = df1.groupBy("review_id").agg(count("*").alias("count"))

duplicate_review_ids.filter(duplicate_review_ids["count"] > lit(1)).show()

+---------+-----+
|review_id|count|
+---------+-----+
+---------+-----+



In [0]:
df2 = df.alias("copy")

In [0]:
df2 = df2.withColumn("text_length", length(df2["text"]))
display(df2)

review_id user_id business_id stars useful funny cool text date text_length l3-NvFb9CZ5kyozZimeOVw NngzzY7_E1OciTrIoKx2uA NDzQFHW671hbB-aArOy12A 3.0 0 0 0 Food is overpriced for the quantity and quality. Service was not warm and friendly. Was pretty excited seeing photos, left a bit hungry having paid $45 for a quick meal for my wife and I. 2021-09-30T21:42:01.000+0000 187 4tkZGQPmhCBpgNDZdBavVw HYozx6QC9nOHb6VeXZLudA jRpK8oG_8QKaPGaaKiCyng 4.0 0 0 0 Great pizza, good service and cool atmosphere. Nice option for anyone who needs gluten free options. 2014-08-09T17:24:52.000+0000 100 _-il7JuW4Cvl1t8mHhd4Ew a1qd8VKm8ideNJZT1lKRLQ ehqT-Pek95bMYQKx5_nKsg 5.0 0 0 0 This was a great choice for our 5th anniversary! It's beautiful, historic and romantic. It's small and gorgeous - such a cool vibe! We had the chicken which was excellent, the pork shank (oh my word!) and the bourbon creme brûlée. It was all amazing and we keep talking about it as one of our new favorite spots in Tampa. 2020-12-13T19:04:52.000+0000 323 vY63xTGQsxU8YzWlhKbsvw Mu7efJ4vtjTSSRm0GKrVZg ShBW2Fx5RvPqYxwRDQAfZA 5.0 0 0 0 I mentioned to them that The "Jack Snow - On The Go" youtube said it wasn't open one day and whined and cried like a little girl so they COMPED my buddy and me a large pepperoni pie and two sausage calzones along with two sodas.

As we finished the meal and started to leave, Manny said. "Wait, there's MORE! Take this home for your families for dinner" and then gave us two spaghetti dinners, two lasagna dinners, four salads, garlic bread and four meatball subs to take home for the kids. 

A total haul of about $100 for free. SCORE!!

I love Manny's House of Pizza. Take that Jack Snow! 2018-07-15T02:09:23.000+0000 590 lMugSxDDDdJF7crcLBwwww weVmDqYqax565OAQ9Y08Yw l4lfhwS8dEhy3MZ3AW1S3Q 1.0 2 1 1 Still worst service ever.... Low grade dog food.

Ordered a buffalo Chicken, got a piece of chicken with buffalo sauce on one side and tomato sauce on the other. they shoudl close this place it's awful!

Only reason I went back is someone gave me a gift card. 2009-01-27T12:29:46.000+0000 262 rQAtM9jo1UJns1WlVjr3OQ NLB0xCtPqCQpRwbht-FCww GdX5jRGWpvEm6KEkdrXq1A 5.0 0 0 0 I love Chipotle. Especially this one place because the staff is always so nice and fast. I also feel they give a bit more customer service, but I always tip so maybe that is why they make sure to make me happy. 2016-09-05T21:10:47.000+0000 210 JRyMpb6NBWvkQnZNO-5zMg 0u1hUugGxvzM_gEg8NT8Tg Wl7iw_u4WeEreF4ZZF1oDw 2.0 3 2 2 Wow this placed has changed...

I use to live in walking distance to Four Rivers and loved getting their takeout....However, things have changed!

After a bad experience about 6 months ago I gave four rivers two more chances and have been let down both times. The past two times I have ordered the General tso's chicken and chicken and broccoli (pretty simple stuff) and was grossed out both times...the meat in the general tso's was soft and mushy not crispy and the chicken and broccoli was soggy and chicken rubbery...I'm sorry Four Rivers I gave you two chances to make up with me and now I refuse to get burned for a third time...time to move on. 2015-06-24T00:59:42.000+0000 651 6XmqzKyiL1-NEy6hU8pGJQ quqkZJJSm79L6ghOFvvY3w kxOR-Z62MnMUlCZWQmd2iQ 3.0 9 7 10 Food was OK and service was a bit slow for Saturday Lunch. Cool Place though. I would come back again for sure. 2016-03-26T21:39:43.000+0000 111 9aMk8hFg4lTgloM_2OA7Iw dGE8IvYm8AZovtYJrpzYCg 1O0teX-jRsmxqDYmRNncSg 1.0 0 0 0 I just spent almost 40 dollars for cold food. I normally love Lion's Choice but I wouldn't recommend this location. It was awful. 2018-07-13T00:43:13.000+0000 129 dwYTuqgNHKo8VKrtJ-6jmA gpXVJ9jljKiwKdA2nVnVLg kSHgckYR4YMaWiMNT8arZA 5.0 0 0 0 I have to say that this place offers a great menu and really filling portions. We ordered the Bert Omlette with a side of gravy along with Ds potato cakes. The service was amazing too!!. If you are driving into or out of Tuscon it is a must for breakfast. Oh...and they

Databricks visualization. Run in Databricks to view.

In [0]:
nlp = spacy.load("en_core_web_sm")

In [0]:
def preprocess_text_spacy(text):
    doc = nlp(text)
    cleaned_text = " ".join(token.text.lower() for token in doc if not token.is_stop and token.is_alpha)
    return cleaned_text

In [0]:
preprocess_udf = udf(preprocess_text_spacy, StringType())
df2 = df2.withColumn("cleaned_text", preprocess_udf(col("text")))

In [0]:
cleaned_words_list = df2.select("cleaned_text").rdd.flatMap(lambda row: row[0].split()).collect()

java.io.IOException: Connection failed
	at com.databricks.rpc.Jetty9Client$$anon$1.handleError(Jetty9Client.scala:826)
	at com.databricks.rpc.Jetty9Client$$anon$1.onFailure(Jetty9Client.scala:753)
	at shaded.v9_4.org.eclipse.jetty.client.ResponseNotifier.notifyFailure(ResponseNotifier.java:197)
	at shaded.v9_4.org.eclipse.jetty.client.ResponseNotifier.notifyFailure(ResponseNotifier.java:189)
	at shaded.v9_4.org.eclipse.jetty.client.HttpExchange.notifyFailureComplete(HttpExchange.java:275)
	at shaded.v9_4.org.eclipse.jetty.client.HttpExchange.abort(HttpExchange.java:247)
	at shaded.v9_4.org.eclipse.jetty.client.HttpConversation.abort(HttpConversation.java:164)
	at shaded.v9_4.org.eclipse.jetty.client.HttpRequest.abort(HttpRequest.java:821)
	at shaded.v9_4.org.eclipse.jetty.client.HttpDestination.abort(HttpDestination.java:559)
	at shaded.v9_4.org.eclipse.jetty.client.HttpDestination.failed(HttpDestination.java:313)
	at com.databricks.rpc.AbstractConnectionPool$1.failed(AbstractConnectionPool.java:161)
	at shaded.v9_4.org.eclipse.jetty.util.Promise$Wrapper.failed(Promise.java:136)
	at com.databricks.rpc.Jetty9Client$DatabricksHttpDestinationOverHTTP$$anon$2.failed(Jetty9Client.scala:1613)
	at shaded.v9_4.org.eclipse.jetty.util.Promise$Wrapper.failed(Promise.java:136)
	at shaded.v9_4.org.eclipse.jetty.client.HttpClient$1$1.failed(HttpClient.java:660)
	at shaded.v9_4.org.eclipse.jetty.client.AbstractConnectorHttpClientTransport.connectFailed(AbstractConnectorHttpClientTransport.java:138)
	at shaded.v9_4.org.eclipse.jetty.client.AbstractConnectorHttpClientTransport$ClientSelectorManager.connectionFailed(AbstractConnectorHttpClientTransport.java:188)
	at shaded.v9_4.org.eclipse.jetty.io.ManagedSelector$Connect.failed(ManagedSelector.java:966)
	at shaded.v9_4.org.eclipse.jetty.io.ManagedSelector.processConnect(ManagedSelector.java:369)
	at shaded.v9_4.org.eclipse.jetty.io.ManagedSelector.access$1700(ManagedSelector.java:65)
	at shaded.v9_4.org.eclipse.jetty.io.ManagedSelector$SelectorProducer.processSelected(ManagedSelector.java:676)
	at shaded.v9_4.org.eclipse.jetty.io.ManagedSelector$SelectorProducer.produce(ManagedSelector.java:535)
	at shaded.v9_4.org.eclipse.jetty.util.thread.strategy.EatWhatYouKill.produceTask(EatWhatYouKill.java:362)
	at shaded.v9_4.org.eclipse.jetty.util.thread.strategy.EatWhatYouKill.doProduce(EatWhatYouKill.java:186)
	at shaded.v9_4.org.eclipse.jetty.util.thread.strategy.EatWhatYouKill.tryProduce(EatWhatYouKill.java:173)
	at shaded.v9_4.org.eclipse.jetty.util.thread.strategy.EatWhatYouKill.run(EatWhatYouKill.java:131)
	at shaded.v9_4.org.eclipse.jetty.util.thread.ReservedThreadExecutor$ReservedThread.run(ReservedThreadExecutor.java:409)
	at com.databricks.rpc.ShadedInstrumentedQueuedThreadPool$$anon$2.$anonfun$run$6(InstrumentedQueuedThreadPool.scala:134)
	at scala.runtime.java8.JFunction0$mcV$sp.apply(JFunction0$mcV$sp.java:23)
	at com.databricks.instrumentation.QueuedThreadPoolInstrumenter.trackActiveThreads(QueuedThreadPoolInstrumenter.scala:66)
	at com.databricks.instrumentation.QueuedThreadPoolInstrumenter.trackActiveThreads$(QueuedThreadPoolInstrumenter.scala:63)
	at com.databricks.rpc.ShadedInstrumentedQueuedThreadPool.trackActiveThreads(InstrumentedQueuedThreadPool.scala:100)
	at com.databricks.rpc.ShadedInstrumentedQueuedThreadPool$$anon$2.run(InstrumentedQueuedThreadPool.scala:129)
	at shaded.v9_4.org.eclipse.jetty.util.thread.QueuedThreadPool.runJob(QueuedThreadPool.java:883)
	at shaded.v9_4.org.eclipse.jetty.util.thread.QueuedThreadPool$Runner.run(QueuedThreadPool.java:1034)
	at java.base/java.lang.Thread.run(Thread.java:829)
Caused by: java.net.ConnectException: Connection refused
	at java.base/sun.nio.ch.SocketChannelImpl.checkConnect(Native Method)
	at java.base/sun.nio.ch.SocketChannelImpl.finishConnect(SocketChannelImpl.java:777)
	at shaded.v9_4.org.eclipse.jetty.io.SelectorManager.doFinishConnect(SelectorManager.java:355)
	at shaded.v9_4.org.eclipse.jetty.io.ManagedSelector.processConnect(

In [0]:
display(df2.limit(5))

review_id user_id business_id stars useful funny cool text date text_length cleaned_text l3-NvFb9CZ5kyozZimeOVw NngzzY7_E1OciTrIoKx2uA NDzQFHW671hbB-aArOy12A 3.0 0 0 0 Food is overpriced for the quantity and quality. Service was not warm and friendly. Was pretty excited seeing photos, left a bit hungry having paid $45 for a quick meal for my wife and I. 2021-09-30T21:42:01.000+0000 187 food overpriced quantity quality service warm friendly pretty excited seeing photos left bit hungry having paid quick meal wife 4tkZGQPmhCBpgNDZdBavVw HYozx6QC9nOHb6VeXZLudA jRpK8oG_8QKaPGaaKiCyng 4.0 0 0 0 Great pizza, good service and cool atmosphere. Nice option for anyone who needs gluten free options. 2014-08-09T17:24:52.000+0000 100 great pizza good service cool atmosphere nice option needs gluten free options _-il7JuW4Cvl1t8mHhd4Ew a1qd8VKm8ideNJZT1lKRLQ ehqT-Pek95bMYQKx5_nKsg 5.0 0 0 0 This was a great choice for our 5th anniversary! It's beautiful, historic and romantic. It's small and gorgeous - such a cool vibe! We had the chicken which was excellent, the pork shank (oh my word!) and the bourbon creme brûlée. It was all amazing and we keep talking about it as one of our new favorite spots in Tampa. 2020-12-13T19:04:52.000+0000 323 great choice anniversary beautiful historic romantic small gorgeous cool vibe chicken excellent pork shank oh word bourbon creme brûlée amazing talking new favorite spots tampa vY63xTGQsxU8YzWlhKbsvw Mu7efJ4vtjTSSRm0GKrVZg ShBW2Fx5RvPqYxwRDQAfZA 5.0 0 0 0 I mentioned to them that The "Jack Snow - On The Go" youtube said it wasn't open one day and whined and cried like a little girl so they COMPED my buddy and me a large pepperoni pie and two sausage calzones along with two sodas.

As we finished the meal and started to leave, Manny said. "Wait, there's MORE! Take this home for your families for dinner" and then gave us two spaghetti dinners, two lasagna dinners, four salads, garlic bread and four meatball subs to take home for the kids. 

A total haul of about $100 for free. SCORE!!

I love Manny's House of Pizza. Take that Jack Snow! 2018-07-15T02:09:23.000+0000 590 mentioned jack snow youtube said open day whined cried like little girl comped buddy large pepperoni pie sausage calzones sodas finished meal started leave manny said wait home families dinner gave spaghetti dinners lasagna dinners salads garlic bread meatball subs home kids total haul free score love manny house pizza jack snow lMugSxDDDdJF7crcLBwwww weVmDqYqax565OAQ9Y08Yw l4lfhwS8dEhy3MZ3AW1S3Q 1.0 2 1 1 Still worst service ever.... Low grade dog food.

Ordered a buffalo Chicken, got a piece of chicken with buffalo sauce on one side and tomato sauce on the other. they shoudl close this place it's awful!

Only reason I went back is someone gave me a gift card. 2009-01-27T12:29:46.000+0000 262 worst service low grade dog food ordered buffalo chicken got piece chicken buffalo sauce tomato sauce shoudl close place awful reason went gave gift card